<a href="https://colab.research.google.com/github/munkefrugt/StockPrograms/blob/main/backtest2years.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>




The goal in this sript is to test the 2 year data for 50 stocks from spy that we have gathered from alpha vantage.
The stocks are taken from different sectors chosen by chat gpt.



#TODO

1 filter the stocks so that its the right to that is used. dont used exteded hours. like from 4 am - 7.30 pm only 9.30 am -4 pm

2 see how many buy signals there will be when when there is a strict filter. like crosses of ema's 2000, 1000, 200, 50.
3 there is still not implemented multiple take profit i think.
4 test with more stocks like 10 in down going SPY periodes. Aim is to have more than 50 % win rate. hopefully 60-70% with 1.5 risk reward ratio

In [ ]:
top50symbols = ['AAPL', 'MSFT', 'AMZN', 'META', 'GOOGL', 'BRK-B', 'JNJ', 'V', 'PG','JPM',
                'UNH', 'MA', 'INTC', 'VZ', 'HD', 'T', 'PFE', 'MRK', 'PEP', 'CSCO',
                'BA','XOM', 'KO', 'CVX', 'NEE', 'CMCSA', 'ORCL', 'DIS', 'ACN', 'IBM',
                'TXN','QCOM', 'MCD', 'ABT', 'MDT', 'NKE', 'AVGO','GILD', 'COST', 'HON',
                'UNP','MMM', 'AMGN', 'BAC', 'WFC', 'USB', 'GS', 'MS', 'BLK', 'JNJ']

In [ ]:
import pandas as pd
import numpy as np

import plotly.graph_objects as go

from plotly.subplots import make_subplots
import math

import os
import pdb

In [ ]:
#pip install --upgrade plotly




#load Drive


In [ ]:
from google.colab import drive
drive.flush_and_unmount()
drive.mount('/content/drive')


Drive not mounted, so nothing to flush and unmount.
Mounted at /content/drive


#Get indicators and data

In [ ]:
import os
import pandas as pd
import numpy as np
import yfinance as yf

df_master = pd.DataFrame(columns=["Ticker", "Df", "Df_buy_signals","Num_of_signals", "Trades"])

# Point to the directory where your .csv files are located
folder_path = '/content/drive/MyDrive/Colab Notebooks/stock data'

# Get the list of all files in directory
file_list = os.listdir(folder_path)

# Filter out all files that are not .csv
csv_files = [file for file in file_list if file.endswith(".csv")]

# Extract ticker symbols from file names
tickers = [file.split('_')[0] for file in csv_files]
def get_daily_df(df):
  df_30m= df
  # # Assuming 'Time' column contains date-time data
  # df_30m['Time'] = pd.to_datetime(df_30m['Time'])
  df_daily = df_30m.resample('D').agg({'Open': 'first', 'High': 'max', 'Low': 'min', 'Close': 'last'})
  # change column names by adding '_daily'
  df_daily.columns = [str(col) + '_daily' for col in df_daily.columns]
  df_daily = df_daily.dropna()

  return df

def get_indicators(df):
    #df = df.drop(df.columns[-1], axis=1)
    #df
    # Calculate technical indicators
    # Tenkan-Sen (Conversion Line): (9-day high + 9-day low)/2
    df['tenkan_sen'] = (df['High'].rolling(window=9).max() + df['Low'].rolling(window=9).min()) / 2

    # Kijun-Sen (Base Line): (26-day high + 26-day low)/2
    df['kijun_sen'] = (df['High'].rolling(window=26).max() + df['Low'].rolling(window=26).min()) / 2

    # Senkou Span A (Leading Span A): (Conversion Line + Base Line)/2
    df['senkou_span_a'] = ((df['tenkan_sen'] + df['kijun_sen']) / 2).shift(26)

    # Senkou Span B (Leading Span B): (52-day high + 52-day low)/2
    df['senkou_span_b'] = ((df['High'].rolling(window=52).max() + df['Low'].rolling(window=52).min()) / 2).shift(26)

    # Chikou Span (Lagging Span): Close plotted 26 days in the past
    df['chikou_span'] = df['Close'].shift(-26)


    df['EMA50'] = df['Close'].ewm(span=50, adjust=False).mean()
    df['EMA100'] = df['Close'].ewm(span=100, adjust=False).mean()
    df['EMA200'] = df['Close'].ewm(span=200, adjust=False).mean()
    df['EMA500'] = df['Close'].ewm(span=500, adjust=False).mean()
    df['EMA2000'] = df['Close'].ewm(span=2000, adjust=False).mean()

    # Calculate MACD
    df['EMA12'] = df['Close'].ewm(span=12, adjust=False).mean()
    df['EMA26'] = df['Close'].ewm(span=26, adjust=False).mean()
    df['MACD'] = df['EMA12'] - df['EMA26']
    df['Signal'] = df['MACD'].ewm(span=9, adjust=False).mean()

    # Calculate Donchian channel
    window = 20
    df['Upper_band'] = df['High'].rolling(window=window).max()
    df['Stop_loss'] = df['Low'].rolling(window=window).min()
    df['Upper_band_1000'] = df['High'].rolling(window=1000).max()

    # drop first stoploss nan rows
    df = df.iloc[window:]

    return df


def is_flat(s, window):
        return s.rolling(window).std() <= 1e-5

def get_df_buy_signals(df, df_daily):
    df['EMA200_Direction'] = np.where(df['EMA200'] > df['EMA200'].shift(1), 1, -1)
    df['EMA50_Direction'] = np.where(df['EMA50'] > df['EMA50'].shift(1), 1, -1)

    # Ensure EMA data is in datetime index for easy comparison
    df_daily.index = pd.to_datetime(df_daily.index)
    df.index = pd.to_datetime(df.index)

    # Creating a DataFrame with the same index as `df`
    df_daily_resampled = pd.DataFrame(index=df.index)

    # Calculate the resampled daily data
    daily_resampled = df_daily.resample('30min').ffill()

    # Now we fill our DataFrame with the daily EMA50 and EMA200 from `daily_resampled`
    df_daily_resampled['EMA50'] = daily_resampled['EMA50']
    df_daily_resampled['EMA200'] = daily_resampled['EMA200']

    # We use `ffill` to fill NaN values (which may occur in the beginning of `df_daily_resampled`)
    df_daily_resampled.ffill(inplace=True)

    # Daily EMA comparison condition
    df['EMA_Daily_Condition'] = np.where(df_daily_resampled['EMA50'] > df_daily_resampled['EMA200'], 1, -1)

    window = 20
    df['Long_Entry'] = np.where(
        (df['Close'] > df['EMA200']) &
        (df['Close'] > df['EMA200']) &
        (df['EMA50'] > df['EMA200']) &
        (df['EMA200_Direction'] == 1) &
        (df['EMA50_Direction'] == 1) &
        (df['EMA_Daily_Condition'] == 1) &
        (df['Row_Number'] > window),
        1, 0)

    df_buy_signals = df[df['Long_Entry'] == 1]
    df_buy_signals = df_buy_signals.drop(
        ['Row_Number', 'EMA50','EMA100','EMA200','EMA500','EMA2000',
         'EMA12', 'EMA26', 'MACD', 'Signal', 'Upper_band','Long_Entry'],
          axis=1)

    return df, df_buy_signals


def filter_df_for_extended_hours(df):
    # Filter data for regular trading hours
    df['Time'] = pd.to_datetime(df['Time'])
    df['Hour'] = df['Time'].dt.hour + df['Time'].dt.minute / 60
    df = df[(df['Hour'] >= 9.5) & (df['Hour'] <= 16)]
    df = df.drop(columns=['Hour'])
    return df


# Loop over tickers instead of predefined tickers
for ticker in tickers:
    # Load data from csv file instead of downloading
    df = pd.read_csv(f"{folder_path}/{ticker}_intraday.csv")
    df = df.iloc[::-1]   # reverse the DataFrame
    df.columns = df.columns.str.title()
    df = filter_df_for_extended_hours(df)

    df.set_index('Time', inplace=True)
    df.insert(0, "Row_Number", range(1, len(df) + 1))
    df_daily = get_daily_df(df)
    df_daily = get_indicators(df)
    df = get_indicators(df)

    df, df_buy_signals = get_df_buy_signals(df, df_daily)
    num_long_entries = len(df_buy_signals)
    df_trades = pd.DataFrame(columns=["Trade_id","Status", "Entry_time", "Entry_price", "Entry_time", "Exit_price", "Type", "Cash","Equity"])
    df_trades.set_index("Trade_id", inplace=True)
    trades = []
    new_row = {"Ticker": ticker, "Df": df,"Df_buy_signals": df_buy_signals, "Num_of_signals": num_long_entries, "Df_trades": df_trades,"Trades": trades, "Df_daily": df_daily }
    df_master = pd.concat([df_master, pd.DataFrame([new_row])], ignore_index=True)

df_master



<ipython-input-64-7c517e1f6e2e>:78: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-64-7c517e1f6e2e>:79: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-64-7c517e1f6e2e>:99: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-64-7c51

Ticker                                                 Df  \
0    AAPL                       Row_Number        Open   ...   
1    MSFT                       Row_Number        Open   ...   
2    AMZN                       Row_Number      Open     ...   
3    META                       Row_Number      Open     ...   
4   GOOGL                       Row_Number      Open     ...   
5   BRK-B                       Row_Number    Open     Hi...   
6       V                       Row_Number        Open   ...   
7      PG                       Row_Number        Open   ...   
8     JPM                       Row_Number        Open   ...   
9     UNH                       Row_Number        Open   ...   
10     MA                       Row_Number        Open   ...   
11   INTC                       Row_Number       Open    ...   
12     VZ                       Row_Number       Open    ...   
13     HD                       Row_Number        Open   ...   
14      T                       Row_Number       Open    ...   
15    PFE                       Row_Number       Open    ...   
16    MRK                       Row_Number        Open   ...   
17    PEP                       Row_Number        Open   ...   
18   CSCO                       Row_Number       Open    ...   
19     BA                       Row_Number      Open     ...   
20    XOM                       Row_Number        Open   ...   
21     KO                       Row_Number       Open    ...   
22    CVX                       Row_Number        Open   ...   
23    NEE                       Row_Number       Open    ...   
24  CMCSA                       Row_Number       Open    ...   
25   ORCL                       Row_Number        Open   ...   
26    DIS                       Row_Number      Open     ...   
27    ACN                       Row_Number        Open   ...   
28    IBM                       Row_Number        Open   ...   
29    TXN                       Row_Number        Open   ...   
30   QCOM                       Row_Number        Open   ...   
31    MCD                       Row_Number        Open   ...   
32    ABT                       Row_Number        Open   ...   
33    MDT                       Row_Number        Open   ...   
34    NKE                       Row_Number        Open   ...   
35   AVGO                       Row_Number        Open   ...   
36   GILD                       Row_Number       Open    ...   
37   COST                       Row_Number        Open   ...   
38    HON                       Row_Number        Open   ...   
39    UNP                       Row_Number        Open   ...   
40    MMM                       Row_Number        Open   ...   
41   AMGN                       Row_Number        Open   ...   
42    BAC                       Row_Number       Open    ...   
43    WFC                       Row_Number       Open    ...   
44    USB                       Row_Number       Open    ...   
45     GS                       Row_Number        Open   ...   
46     MS                       Row_Number       Open    ...   
47    BLK                       Row_Number        Open   ...   
48    JNJ                       Row_Number        Open   ...   

                                       Df_buy_signals Num_of_signals Trades  \
0                              Open        High   ...           2892     []   
1                              Open        High   ...           2778     []   
2                            Open       High      ...           2044     []   
3                            Open      High       ...           2261     []   
4                             Open        High    ...           2423     []   
5                            Open     High      Lo...           2694     []   
6                              Open        High   ...           2432     []   
7                              Open        High   ...           2822     []   
8                              Open        High   ...           2278     []   
9           

In [ ]:
df_master["Df_daily"].iloc[0]
#df_master["Df"].iloc[0]


Row_Number        Open        High         Low  \
Time                                                                  
2021-06-30 12:30:00          21  134.983254  135.232136  134.928002   
2021-06-30 13:00:00          22  135.120742  135.273946  135.093561   
2021-06-30 13:30:00          23  135.249236  135.461744  135.224525   
2021-06-30 14:00:00          24  135.402439  135.412323  135.140510   
2021-06-30 14:30:00          25  135.353019  135.451860  135.283830   
...                         ...         ...         ...         ...   
2023-06-16 14:00:00        6930  185.570000  185.620000  185.200000   
2023-06-16 14:30:00        6931  185.300000  185.300000  184.861800   
2023-06-16 15:00:00        6932  184.900000  185.025000  184.710000   
2023-06-16 15:30:00        6933  184.920000  185.350000  184.270000   
2023-06-16 16:00:00        6934  184.920000  185.200000  184.901500   

                          Close   Volume  tenkan_sen  kijun_sen  \
Time                                                              
2021-06-30 12:30:00  135.124992  2561796  134.947770        NaN   
2021-06-30 13:00:00  135.251608  1721418  134.947770        NaN   
2021-06-30 13:30:00  135.397497  2148549  134.947770        NaN   
2021-06-30 14:00:00  135.362903  2148680  135.096032        NaN   
2021-06-30 14:30:00  135.333251  2054067  135.244294        NaN   
...                         ...      ...         ...        ...   
2023-06-16 14:00:00  185.310000  1957377  185.630000    184.970   
2023-06-16 14:30:00  184.900000  3899773  185.495900    185.385   
2023-06-16 15:00:00  184.915000  3709686  185.420000    185.385   
2023-06-16 15:30:00  185.010000  8225575  185.149950    185.505   
2023-06-16 16:00:00  184.980000  7761502  185.149950    185.630   

                     senkou_span_a  senkou_span_b  ...      EMA200  \
Time                                               ...               
2021-06-30 12:30:00            NaN            NaN  ...  134.065830   
2021-06-30 13:00:00            NaN            NaN  ...  134.077629   
2021-06-30 13:30:00            NaN            NaN  ...  134.090762   
2021-06-30 14:00:00            NaN            NaN  ...  134.103420   
2021-06-30 14:30:00            NaN            NaN  ...  134.115657   
...                            ...            ...  ...         ...   
2023-06-16 14:00:00        183.205        182.510  ...  180.932817   
2023-06-16 14:30:00        183.205        182.510  ...  180.972291   
2023-06-16 15:00:00        183.170        182.510  ...  181.011522   
2023-06-16 15:30:00        183.610        182.915  ...  181.051308   
2023-06-16 16:00:00        183.930        183.285  ...  181.090400   

                         EMA500     EMA2000       EMA12       EMA26      MACD  \
Time                                                                            
2021-06-30 12:30:00  133.969670  133.917894  134.961920  134.691826  0.270093   
2021-06-30 13:00:00  133.974788  133.919227  135.006487  134.733291  0.273195   
2021-06-30 13:30:00  133.980467  133.920704  135.066642  134.782492  0.284150   
2021-06-30 14:00:00  133.985986  133.922146  135.112221  134.825485  0.286736   
2021-06-30 14:30:00  133.991364  133.923556  135.146226  134.863098  0.283128   
...                         ...         ...         ...         ...       ...   
2023-06-16 14:00:00  175.665562  161.266804  185.622034  185.314742  0.307293   
2023-06-16 14:30:00  175.702426  161.290426  185.510952  185.284020  0.226932   
2023-06-16 15:00:00  175.739203  161.314039  185.419267  185.256685  0.162582   
2023-06-16 15:30:00  175.776212  161.337723  185.356303  185.238412  0.117891   
2023-06-16 16:00:00  175.812954  161.361353  185.298410  185.219271  0.079140   

                       Signal  Upper_band   Stop_loss  Upper_band_1000  
Time                                                                    
2021-06-30 12:30:00  0.258184  135.600122  133.633183              NaN  
2021-06-30 13:00:00  0.261186  135.600122

In [ ]:
import plotly.graph_objects as go
row= 0
df_daily = df_master["Df_daily"].iloc[row]
df_combined = df_master["Df"].iloc[row]
df_buy_signals_special = df_master["Df_buy_signals"].iloc[row]

trace0 = go.Scatter(
    x = df_combined.index,
    y = df_combined['Close'],
    mode = 'lines',
    name = '30m Close'
)

trace1 = go.Scatter(
    x = df_daily.index,
    y = df_daily['Close'],
    mode = 'lines',
    name = 'Daily Close'
)

trace2 = go.Scatter(
    x = df_combined.index,
    y = df_combined['senkou_span_a'],
    mode = 'lines',
    name = '30m Senkou Span A',
    line = dict(color='green')
)

trace3 = go.Scatter(
    x = df_combined.index,
    y = df_combined['senkou_span_b'],
    mode = 'lines',
    name = '30m Senkou Span B',
    line = dict(color='blue')
)

trace4 = go.Scatter(
    x = df_daily.index,
    y = df_daily['senkou_span_a'],
    mode = 'lines',
    name = 'Daily Senkou Span A',
    line = dict(color='yellow')
)

trace5 = go.Scatter(
    x = df_daily.index,
    y = df_daily['senkou_span_b'],
    mode = 'lines',
    name = 'Daily Senkou Span B',
    line = dict(color='red')
)

trace6 = go.Scatter(
    x = df_daily.index,
    y = df_daily.EMA200,
    mode = 'lines',
    name = 'Daily EMA200',
    line = dict(color='black')
)

trace7 = go.Scatter(
    x = df_daily.index,
    y = df_daily.EMA50,
    mode = 'lines',
    name = 'Daily EMA 50',
    line = dict(color='orange')
)

trace8 = go.Scatter(
    x = df_buy_signals_special.index,
    y = df_buy_signals_special['Close'],
    mode = 'markers',
    marker=dict(
        size=10,
        color='green',
        symbol='triangle-up'
    ),
    name = 'Buy Signals'
)

data = [trace0, trace1, trace2, trace3, trace4, trace5,  trace6, trace7, trace8]

layout = go.Layout(
    title='Closing Prices and Ichimoku Clouds Over Time',
    xaxis=dict(title='Time'),
    yaxis=dict(title='Price')
)

fig = go.Figure(data=data, layout=layout)
fig.show()


In [ ]:
import pandas as pd

# Initialize the latest_start_date and earliest_end_date to arbitrary dates
latest_start_date = pd.Timestamp('1900-01-01')
earliest_end_date = pd.Timestamp('2100-01-01')

# Find the latest start date and the earliest end date among all DataFrames
for i, row in df_master.iterrows():
    df = row['Df']

    # Convert 'Time' column to datetime if it's not already
    df['Time'] = pd.to_datetime(df['Time'])

    # Update latest_start_date and earliest_end_date based on the current DataFrame
    latest_start_date = max(latest_start_date, df['Time'].min())
    earliest_end_date = min(earliest_end_date, df['Time'].max())

# Now that we have the common date range, let's truncate each DataFrame
for i, row in df_master.iterrows():
    df = row['Df']

    # Truncate the DataFrame
    df_truncated = df[(df['Time'] >= latest_start_date) & (df['Time'] <= earliest_end_date)]

    # Update the df in df_master
    df_master.at[i, 'Df'] = df_truncated

print(f"DataFrames truncated to the common date range: {latest_start_date} to {earliest_end_date}")


DataFrames truncated to the common date range: 2021-07-02 10:00:00 to 2023-06-16 16:00:00


In [ ]:
df_master.Num_of_signals.sum()


1782

In [ ]:

# shorten df master to AAPL
df_master_copy = df_master.copy()
#only use first line
#df_master_copy = df_master_copy.iloc[22:23]
#df_master_copy.drop(df_master.index[11:12], inplace=True)
df_master_copy = df_master.iloc[[0]].copy()

#df_master_copy = df_master.iloc[[11:12]].copy()
#select only buy signals
#df_master_copy = df_master_copy[df_master_copy["Num_of_signals"] != 0]
df_master_copy


Ticker                                                 Df  \
0   AAPL                       Row_Number       Close  C...   

                                      Df_buy_signals Num_of_signals Trades  \
0                            Close  Close_daily  ...             36     []   

                                           Df_trades  
0  Empty DataFrame
Columns: [Status, Entry_time, ...

In [ ]:
#tickers = df_master_copy.Ticker.item()
tickers = list(df_master_copy["Ticker"])

len(tickers)

1

In [ ]:
df_master_copy.iloc[0]["Df"].Stop_loss
df =df_master_copy

In [ ]:
#df['Stop_loss'] = df['Low'].rolling(window=window).min()
df_AAPL = df_master_copy.iloc[0]["Df"]
df_AAPL['Stop_loss'] = df_AAPL['Low'].rolling(window=20).min()

df_AAPL['Stop_loss'].head(20)

Time
2021-07-02 10:00:00           NaN
2021-07-02 10:30:00           NaN
2021-07-02 11:00:00           NaN
2021-07-02 11:30:00           NaN
2021-07-02 12:00:00           NaN
2021-07-02 12:30:00           NaN
2021-07-02 13:00:00           NaN
2021-07-02 13:30:00           NaN
2021-07-02 14:00:00           NaN
2021-07-02 14:30:00           NaN
2021-07-02 15:00:00           NaN
2021-07-02 15:30:00           NaN
2021-07-02 16:00:00           NaN
2021-07-06 09:30:00           NaN
2021-07-06 10:00:00           NaN
2021-07-06 10:30:00           NaN
2021-07-06 11:00:00           NaN
2021-07-06 11:30:00           NaN
2021-07-06 12:00:00           NaN
2021-07-06 12:30:00    136.786215
Name: Stop_loss, dtype: float64

#Backtest

In [ ]:
import math
timeline = df_master_copy.iloc[0]["Df"].Time
# get asending order of time
timeline = timeline.sort_values()


# keep all the details about the trades
master_trades_df = pd.DataFrame(columns=[
    "trade_id", "cash", "cash_after_sell", "equity","cash_spend", "profit", "max_loss", "entry_time","entry_price", "exit_time","exit_price",
    "position_size", "tp", "sl", "exit_type","ticker","status"])
#master_trades_df.index.name = "trade_id"

#current_ticker_prices = pd.DataFrame(columns=['tickers', 'price', 'position_size','value'])

# Add tickers to the DataFrame
# current_ticker_prices['tickers'] = tickers
# current_ticker_prices['position_size'] = 0
# current_ticker_prices['price'] = 0
# current_ticker_prices['value'] = 0

cash_equity_df = pd.DataFrame(columns=['time', 'cash', 'equity'])
cash_equity_df['time'] = timeline
cash_equity_df['cash'] = 0
cash_equity_df['equity'] = 0
cash_equity_df.set_index('time', inplace=True)

start_capital = 100000
equity=None
cash = start_capital
risk_percentage = 0.02
# for trade objects
trades = []
winning_streak = 0
losing_streak = 0
max_winning_streak = 0
max_losing_streak = 0
total_wins = 0
total_losses = 0


class Trade:
    # initialize the class with the next ID
    next_id = 1

    def __init__(self, entry_price):
        self.entry_price = entry_price
        self.sl = None
        self.tp = None
        self.position_size = None
        self.entry_time = None
        self.current_open_price = None
        self.ticker = None
        self.trade_id = Trade.next_id  # assign the next available ID
        Trade.next_id += 1  # increment the next available ID
        self.status = "open"


for time in timeline:
    #store cash  equity for printing
    cash_equity_df.loc[time, "cash"] = cash
    cash_equity_df.loc[time, "equity"] = equity
    #pdb.set_trace()
    # Loop through the master row by row. check for signals.
    for index, row in df_master_copy.iterrows():
        #print("index " + str(index))
        ticker = row["Ticker"]
        #print(ticker)

        df = row["Df"]
        #print(df)
        #df_buy_signals = row["Df_buy_signals"]
        #df_trades = row["Df_trades"]

        #trades = row["Trades"]
        #print(time)
        # get the row of the df with the time we are at
        current_row = df[df['Time'] == time]
        #pdb.set_trace()
        #print(current_row)
        #print(current_row["Long_Entry"].item())
        if current_row.empty:
          #print(f"No data available for time {time} for ticker {ticker}")
          continue

        signal = current_row["Long_Entry"].item()
        open_price = current_row["Open"].item()
        current_price = open_price
        low_price = current_row["Low"].item()
        high_price = current_row["High"].item()
        ema500 = current_row.EMA500.item()
        sl = None

        # make an aproximate equity.

        value = 0
        for trade in trades:
          if trade.status== "open":
            value = value + trade.entry_price* trade.position_size
        aproximate_equity = value + cash
        equity = aproximate_equity

        # Check for buy signals
        if signal == 1:

          print("\n")
          print("Buy signal for ticker", ticker, "at time", time)
          print("equity: " + str(equity))

          #print(current_row)
          #print(total_position_amount)
          sl = current_row["Stop_loss"].item()
          print(cash)
          risk = open_price - sl
          print(open_price)
          print(sl)
          print(risk)
          if cash >= current_price and risk > 0:
            max_position_size = (equity * risk_percentage) / risk
            position_size = math.floor(max_position_size)
            print("max position size "  + str(position_size))
            potential_spending = position_size * current_price

            max_loss = equity * risk_percentage
            potential_loss = position_size* risk

            if potential_spending > cash:
              # error its not the right position size. It need to be smaller.
              position_size = math.floor(cash / current_price)
              potential_spending = position_size *current_price
              print("change position amount to " + str(position_size))
            else:

              print("use max position size "  + str(position_size))

            #make the trade:
            if potential_loss <= max_loss :
              print("we can trade")
              print("potential_loss " + str(potential_loss))
              potential_loss_over_equity = potential_loss/ equity
              #df.loc[i, "Potential_loss_over_equity_pct"] = potential_loss_over_equity * 100

              print("potential_spending " + str(potential_spending))
              print("buy position size "  + str(position_size))

              cash =cash- potential_spending
              print("cash left " +str(cash))



              # Open a new trade
              print("Open Trade ! <-------------")

              # add trade
              trade = Trade(entry_price=open_price)
              trade.sl = sl
              trade.tp = open_price + risk*1.5
              trade.position_size = position_size
              trade.entry_time = time
              trade.ticker = ticker
              trades.append(trade)
              print("trade_id : " + str(trade.trade_id))

              # fill master_trades_df
              trade_dict = {
                  "trade_id": trade.trade_id,
                  "cash" : cash,
                  "equity": equity,
                  "cash_spend": potential_spending,

                  #"profit": 0,
                  "max_loss": max_loss,
                  "entry_time": trade.entry_time,
                  "entry_price": trade.entry_price,
                  # "exit_time": ,
                  # "exit_price": ,
                  "position_size": trade.position_size,
                  "position*price": 0,
                  "cash after sell": 0,
                  "tp": trade.tp,
                  "sl": trade.sl,
                  #"type": "tp",
                  "ticker": ticker,
                  "status": trade.status

              }
              master_trades_df.loc[trade.trade_id] = trade_dict



              # df_trades["Trade_id"] = trade.trade_id
              #print(trade.trade_id)
              # df_trades[ "Time"] = time
              # df_trades[ "Buy_price"] = open_price
              # df_trades[ "Status"] = "open"
          else:
            print(" ''''''''''''''''''''''''''''''''''''' not enough cash to trade or no risk availible, risk = : " + str(risk))



        for trade in trades:
            if trade.status == "open":
              #stoploss
              if low_price <= trade.sl: # or low_price <= ema500
                  print(f"Stopped out trade with entry price {trade.entry_price}")
                  print("trade_id : "+ str(trade.trade_id))
                  trade.status = "closed"
                  master_trades_df.loc[trade.trade_id,'status'] = "closed"
                  master_trades_df.loc[trade.trade_id,'exit_type'] = "sl"
                  master_trades_df.loc[trade.trade_id,'exit_time'] = time
                  aproximate_sell_price= trade.sl
                  # if low_price <= ema500 :
                  #   aproximate_sell_price = ema500
                  #   master_trades_df.loc[trade.trade_id,'exit_type'] = "Ema500Stop"


                  master_trades_df.loc[trade.trade_id,'exit_price'] = aproximate_sell_price


                  #cash = cash + low_price * trade.position_size
                  master_trades_df.loc[trade.trade_id,'cash_after_sell'] = cash
                  cash_spend = trade.entry_price * trade.position_size
                  #aproximate
                  cash_return = aproximate_sell_price * trade.position_size
                  profit = cash_return-cash_spend
                  master_trades_df.loc[trade.trade_id,'profit'] =  profit

                  # update cash:
                  print("cash before update: " + str(cash))
                  cash = cash + cash_return
                  print("cash after update: " + str(cash))

                  print("profit: " + str(profit))
                  print("cash_return: " + str(cash_return) + " cash_spend: " + str(cash_spend))
                  print("entry price: " + str(trade.entry_price))
                  print("entry price: " + str(trade.entry_price))


                  total_losses += 1
                  losing_streak += 1
                  winning_streak = 0
                  if losing_streak > max_losing_streak:
                      max_losing_streak = losing_streak



              #take profit
              elif high_price >= trade.tp:
                  print(f"Take profit hit for trade with entry price {trade.entry_price}")
                  print("trade_id : "+ str(trade.trade_id))

                  trade.status = "closed"
                  master_trades_df.loc[trade.trade_id,'status'] = "closed"
                  master_trades_df.loc[trade.trade_id,'exit_type'] = "tp"
                  master_trades_df.loc[trade.trade_id,'exit_time'] = time
                  master_trades_df.loc[trade.trade_id,'exit_price'] = trade.tp

                  cash = cash + trade.tp * trade.position_size
                  master_trades_df.loc[trade.trade_id,'cash_after_sell'] = cash
                  cash_spend = trade.entry_price * trade.position_size
                  cash_return = trade.tp * trade.position_size
                  master_trades_df.loc[trade.trade_id,'profit'] = cash_return-cash_spend

                  #update winners
                  total_wins += 1
                  winning_streak += 1
                  losing_streak = 0
                  if winning_streak > max_winning_streak:
                      max_winning_streak = winning_streak

#print(current_ticker_prices)

#df_trades = df_master.iloc[0]["Df_trades"]
#df_trades

# Print the results
total_trades = total_wins + total_losses
#win_rate = total_wins / total_trades


print("Total number of winning trades:", total_wins)
print("Total number of losing trades:", total_losses)
print("Maximum consecutive winning trades:", max_winning_streak)
print("Maximum consecutive losing trades:", max_losing_streak)
#print("Win rate:", win_rate)
master_trades_df
#current_ticker_prices



Buy signal for ticker AAPL at time 2021-07-21 10:00:00
equity: 100000
100000
143.5963675355049
140.11716039257396
3.4792071429309317
max position size 574
use max position size 574
we can trade
potential_loss 1997.0649000423548
potential_spending 82424.31496537982
buy position size 574
cash left 17575.685034620183
Open Trade ! <-------------
trade_id : 1


Buy signal for ticker AAPL at time 2021-07-21 14:30:00
equity: 100000.0
17575.685034620183
143.45868186646788
142.95390030740688
0.5047815590610014
max position size 3962
change position amount to 122
we can trade
potential_loss 1999.9445369996877
potential_spending 17501.959187709082
buy position size 122
cash left 73.72584691110023
Open Trade ! <-------------
trade_id : 2
Take profit hit for trade with entry price 143.45868186646788
trade_id : 2


Buy signal for ticker AAPL at time 2021-07-30 14:00:00
equity: 100092.37502530817
17668.060059928343
144.05597870637467
142.43992652492815
1.6160521814465199
max position size 1238
chan

trade_id          cash  cash_after_sell         equity     cash_spend  \
1          1  17575.685035    103383.709925  100000.000000   82424.314965   
2          2     73.725847     17668.060060  100000.000000   17501.959188   
3          3     93.230658     17963.797609  100092.375025   17574.829402   
4          4     86.645508        86.645508  103383.709925  103297.064416   
5          5   1707.050908    103316.326405  101869.989314  100162.938406   
6          6     97.569540    104970.062945  101869.989314    1609.481369   
7          7     66.384201    105322.253348  104970.062945  104903.678744   
8          8     84.201035    106459.814446  105322.253348  105238.052313   
9          9  25044.155245    109653.045104  106459.814446   81415.659201   
10        10    129.815093    111294.228585  109653.045104  109523.230011   
11        11     99.479950        99.479950  111294.228585  111194.748635   
12        12     39.864270    110193.269524  109862.649331  109822.785061   
13        13     14.884011    110946.863371  110193.269524  110178.385513   
14        14     70.663336        70.663336  110946.863371  110876.200035   
15        15    143.811606    113086.362883  109941.861068  109798.049462   
16        16    121.592507    113152.862899  113086.362883  112964.770376   
17        17     51.597352    115028.494383  113152.862899  113101.265547   
18        18     24.049383        24.049383  115028.494383  115004.445000   
19        19    108.809383    116504.689383  114423.049383  114314.240000   
20        20    162.244383    116961.281883  116504.689383  116342.445000   
21        21    131.711883    118786.796883  116961.281883  116829.570000   

         profit     max_loss          entry_time  entry_price  \
1   2995.597350  2000.000000 2021-07-21 10:00:00   143.596368   
2     92.375025  2000.000000 2021-07-21 14:30:00   143.458682   
3    295.737549  2001.847501 2021-07-30 14:00:00   144.055979   
4  -1513.720610  2067.674198 2021-08-16 12:30:00   147.146815   
5   3055.818460  2037.399786 2021-08-20 10:00:00   146.010114   
6     44.255171  2037.399786 2021-08-20 12:30:00   146.316488   
7    352.190403  2099.401259 2021-11-16 11:00:00   148.378612   
8   1137.561098  2106.445067 2021-12-15 14:00:00   171.957602   
9   3193.230658  2129.196289 2021-12-22 10:30:00   172.126129   
10  1641.183481  2193.060902 2022-02-08 11:00:00   171.397856   
11 -1431.579255  2225.884572 2022-08-25 15:00:00   168.476892   
12   330.620193  2197.252987 2023-03-20 10:00:00   154.245485   
13   753.593847  2203.865390 2023-03-24 11:30:00   158.075159   
14 -1005.002303  2218.937267 2023-04-06 11:00:00   163.053235   
15  3144.501816  2198.837221 2023-04-13 10:00:00   162.663777   
16    66.500016  2261.727258 2023-04-20 15:30:00   165.394979   
17  1875.631484  2263.057258 2023-04-26 11:30:00   164.391374   
18  -605.445000  2300.569888 2023-05-15 11:00:00   171.905000   
19  2081.640000  2288.460988 2023-05-16 13:30:00   172.160000   
20   456.592500  2330.093788 2023-05-22 11:00:00   173.905000   
21  1825.515000  2339.225638 2023-05-25 12:00:00   172.315000   

              exit_time  exit_price  position_size          tp          sl  \
1   2021-08-16 09:30:00  148.815178            574  148.815178  140.117160   
2   2021-07-22 09:30:00  144.215854            122  144.215854  142.953900   
3   2021-08-12 10:30:00  146.480057            122  146.480057  142.439927   
4   2021-08-18 15:30:00  144.990518            702  150.381261  144.990518   
5   2021-08-30 10:30:00  150.464660            686  150.464660  143.040417   
6   2021-08-30 10:30:00  150.339685             11  150.339685  143.634357   
7   2021-11-16 11:00:00  148.876760            707  148.876760  148.046514   
8   2021-12-15 14:00:00  173.816362            612  173.816362  170.718429   
9   2021-12-27 16:00:00  178.877146            473  178.877146  167.625452   
10  2022-02-08 12:30:00  173.966218            639  173.966218  169.685615   
11  2022-08-26 11:00

In [ ]:
master_trades_df.head(15);

In [ ]:
df_master["Df"].iloc[0].tail(20)

In [ ]:
df_master_copy[df_master_copy["Ticker"] == ticker]["Df"].iloc[0]

Todo :

2. check at den handler rigtigt


-få styr på tiden. det ser ud til at tids columen er mærkelig.  entry_time f.eks er et tal.
- få det plottet.
  - equity
  - cash
  - diverse EMA's
  - entry
  - exit






In [ ]:
tickers = list(df_master_copy["Ticker"])
tickers

['AAPL']

To do :
- only by once per break out of the 20 period break out.
-experiment with 1500 upper band
-only by right around the break out not long after.
-add conditions for break out. there needs to be a conolidation period. of 20 periods where its pretty flat. and then breaks.

-add trailing stop loss or something like that.


In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np

# Create subplots with one row for each ticker
tickers = list(df_master_copy["Ticker"])

num_rows = len(tickers) + 2
row_heights = [0.5] * len(tickers) + [0.1, 0.1] # adjust as needed
fig = make_subplots(rows=num_rows, cols=1, shared_xaxes=True, vertical_spacing=0.01, row_heights=row_heights)

for i, ticker in enumerate(tickers):
    df = df_master_copy[df_master_copy["Ticker"] == ticker]["Df"].iloc[0]
    df_trades = master_trades_df[master_trades_df["ticker"] == ticker]

    # Kumo cloud
    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.senkou_span_a),
                         fill=None, mode='lines', line_color='green', name=f"{ticker} Senkou Span A"), row=i+1, col=1)

    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.senkou_span_b),
                          fill='tonexty', mode='lines', fillcolor='rgba(128, 128, 128, 0.2)', line_color='red', name=f"{ticker} Senkou Span B"), row=i+1, col=1)

    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.chikou_span), name=f"{ticker} Chickou"), row=i+1, col=1)

    #indicators

    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.Close), name=f"{ticker} Close"), row=i+1, col=1)
    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.EMA2000), name=f"{ticker} EMA2000"), row=i+1, col=1)
    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.EMA200), name=f"{ticker} EMA200"), row=i+1, col=1)
    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.EMA50), name=f"{ticker} EMA50"), row=i+1, col=1)
    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.EMA500), name=f"{ticker} EMA500"), row=i+1, col=1)
    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.Stop_loss), name=f"{ticker} Stoploss"), row=i+1, col=1)
    fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.Upper_band), name=f"{ticker} Upper_band"), row=i+1, col=1)



    #fig.add_trace(go.Scatter(x=list(df['Time']), y=list(df.Upper_band_1000), name=f"{ticker} Upper_band_1000"), row=i+1, col=1)

    fig.add_trace(go.Scatter(x=df_trades['entry_time'], y=df_trades['entry_price'], mode='markers',
                             marker=dict(size=30, color='green', symbol='triangle-up'), name=f"{ticker} Buy Signal"), row=i+1, col=1)

    jitter = 0.25
    y = df_trades['exit_price']
    y_jitter = y + np.random.normal(0, jitter, size=len(y))

    fig.add_trace(go.Scatter(x=df_trades['exit_time'], y=y_jitter, mode='markers',
                             marker=dict(size=30, color='red', symbol='triangle-down'), name=f"{ticker} Sell Signal"), row=i+1, col=1)

fig.add_trace(go.Scatter(x=list(cash_equity_df.index), y=list(cash_equity_df.cash),
                         line=dict(color='blue', width=2), name='Cash'), num_rows-1, 1);

fig.add_trace(go.Scatter(x=list(cash_equity_df.index), y=list(cash_equity_df.equity),
                         line=dict(color='blue', width=2), name='Equity'), num_rows, 1);

fig.update_layout(
    height=1000*len(tickers),
    width=1200,
    showlegend=True,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    title="AAPL Opening Hour Timeframe with EMA 200",
    xaxis_title="Time",
    yaxis_title="Price ($)",
    legend_title="Legend",
    xaxis_rangebreaks=[
        dict(bounds=["sat", "mon"]),
        dict(bounds=[16.5, 9.5], pattern="hour"),
    ],
    legend=dict(
        font=dict(
            family="sans-serif",
            size=18,
            color="blue"
        )
    ),
    xaxis=dict(
        rangeselector=dict(
            visible=False
        )
    )
)

fig.update_yaxes(
    title_text="Cash",
    title_font=dict(size=25, family="Arial", color="blue"),
    row=num_rows-1, col=1
)
fig.update_yaxes(
    title_text="Equity",
    title_font=dict(size=25, family="Arial", color="blue"),
    row=num_rows, col=1
)

fig.update_xaxes(tickfont=dict(size=20, family='Arial', color='blue'))
fig.update_yaxes(tickfont=dict(size=20, family='Arial', color='blue'))

fig.show()


In [ ]:
import plotly.graph_objects as go

# Create a figure
fig = go.Figure()

# Add a trace (line) to the figure
fig.add_trace(
    go.Scatter(
        x=list(cash_equity_df.index),
        y=list(cash_equity_df.equity),
        line=dict(color='blue', width=2),
        name='Equity'
    )
)

# Display the figure
fig.show()

#machine learning